In [11]:
import networkx as nx
import gzip
import matplotlib.pyplot as plt
import matplotlib.animation as animation
import random
from IPython.display import HTML


In [19]:
def load_facebook_graph(path):
    G = nx.Graph()
    with gzip.open(path, 'rt') as f:
        for line in f:
            u, v = map(int, line.strip().split())
            G.add_edge(u, v)
    return G


def load_ca_grqc_graph(path):
    G = nx.Graph()
    with gzip.open(path, 'rt') as f:
        for line in f:
            if line.startswith('#'):
                continue
            u, v = map(int, line.strip().split())
            G.add_edge(u, v)
    return G


In [13]:
def independent_cascade(G, seeds, p=0.01, steps=0):
    activated = set(seeds)
    new_activated = set(seeds)
    
    while new_activated:
        next_activated = set()
        for node in new_activated:
            for neighbor in G.neighbors(node):
                if neighbor not in activated:
                    if random.random() <= p:
                        next_activated.add(neighbor)
        new_activated = next_activated
        activated |= new_activated
        if steps and steps <= 0:
            break
        steps -= 1
    return activated


In [14]:
def independent_cascade_steps(G, seeds, p=0.01):
    steps = []
    activated = set(seeds)
    new_activated = set(seeds)
    steps.append(set(seeds))  # Step 0: initial seeds

    while new_activated:
        next_activated = set()
        for node in new_activated:
            for neighbor in G.neighbors(node):
                if neighbor not in activated:
                    if random.random() <= p:
                        next_activated.add(neighbor)
        new_activated = next_activated
        if new_activated:
            steps.append(set(new_activated))
        activated |= new_activated
    return steps

In [15]:
def greedy_influence_maximization(G, k, p=0.01, simulations=10):
    seeds = []
    for _ in range(k):
        best_node = None
        best_spread = 0
        for node in G.nodes():
            if node in seeds:
                continue
            temp_seeds = seeds + [node]
            spread = 0
            for _ in range(simulations):
                spread += len(independent_cascade(G, temp_seeds, p))
            avg_spread = spread / simulations
            if avg_spread > best_spread:
                best_spread = avg_spread
                best_node = node
        seeds.append(best_node)
    return seeds


In [16]:
def animate_ic_spread(G, steps, seeds, layout=None):
    if layout is None:
        layout = nx.spring_layout(G, seed=42)

    fig, ax = plt.subplots(figsize=(12, 8))
    all_activated = set()

    def update(frame):
        ax.clear()
        current = set.union(*steps[:frame+1])
        new_nodes = steps[frame] if frame < len(steps) else set()
        
        colors = []
        for node in G.nodes():
            if node in seeds:
                colors.append('red')
            elif node in new_nodes:
                colors.append('orange')
            elif node in current:
                colors.append('yellow')
            else:
                colors.append('lightgray')

        nx.draw(
            G, pos=layout,
            node_color=colors,
            with_labels=False,
            node_size=20,
            edge_color='gray',
            alpha=0.6,
            ax=ax
        )
        ax.set_title(f"Independent Cascade - Step {frame}")

    ani = animation.FuncAnimation(
        fig, update, frames=len(steps), interval=800, repeat=False
    )
    plt.close(fig)
    return ani


In [ ]:
G = load_facebook_graph('facebook_combined.txt.gz')
print(f"Graph loaded with {G.number_of_nodes()} nodes and {G.number_of_edges()} edges")


Graph loaded with 4039 nodes and 88234 edges


In [8]:
k = 7  # number of seeds
p = 0.05  # influence probability

seeds = greedy_influence_maximization(G, k=k, p=p, simulations=10)
print("Selected seed nodes:", seeds)


Selected seed nodes: [1912, 107, 1684, 2212, 3437, 1985, 1059]


In [9]:
steps = independent_cascade_steps(G, seeds, p=p)

layout = nx.spring_layout(G, seed=42)
ani = animate_ic_spread(G, steps, seeds, layout)

display(HTML(ani.to_jshtml()))



In [20]:
G = load_ca_grqc_graph('ca-GrQc.txt.gz')
print(f"Graph has {G.number_of_nodes()} nodes and {G.number_of_edges()} edges")

Graph has 5242 nodes and 14496 edges


In [28]:
k = 5  # number of seeds
p = 0.3  # influence probability

seeds = greedy_influence_maximization(G, k=k, p=p, simulations=10)
print("Selected seed nodes:", seeds)

Selected seed nodes: [12365, 15244, 13801, 22601, 4743]


In [29]:
steps = independent_cascade_steps(G, seeds, p=p)

layout = nx.spring_layout(G, seed=42)
ani = animate_ic_spread(G, steps, seeds, layout)

display(HTML(ani.to_jshtml()))
